## **6. Generate the Real Schema**

Based on what we've learned about TFDV and about the data, let's take a first stab at actually generating a schema that we can use down the line. 

Let's also generate a schema for the post-transform data. 

Now that we have an idea about the data, we can suggest reasonable constraints to start with:

 + Genre 
     + Must be present in at least 98\% of examples 
     + Must be 100\% within the domain 
     + Skew detection --> L infinity norm of 0.05 
 + Subgenre 
     + Must be present in at least 98\% of examples 
     + Must be 98\% within the domain 
     + Skew detection --> L infinity norm of 0.01
 + Tags 
     + Must be present in at least 98\% of examples 
     + Must be 

In [1]:
import os
import pprint
import tempfile
import urllib

import pandas as pd
from sklearn.model_selection import train_test_split

import absl
import tensorflow as tf
import tensorflow_model_analysis as tfma
import tensorflow_data_validation as tfdv
import tensorflow_transform as tft
tf.get_logger().propagate = False
pp = pprint.PrettyPrinter()

import tfx
from tfx.components import CsvExampleGen
from tfx.components import Evaluator
from tfx.components import ExampleValidator
from tfx.components import Pusher
from tfx.components import ResolverNode
from tfx.components import SchemaGen
from tfx.components import StatisticsGen
from tfx.components import Trainer
from tfx.components import Transform
from tfx.components.base import executor_spec
from tfx.components.trainer.executor import GenericExecutor
from tfx.dsl.experimental import latest_blessed_model_resolver
from tfx.orchestration import metadata
from tfx.orchestration import pipeline
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
from tfx.components.example_gen.custom_executors import parquet_executor 
from tfx.components.example_gen.component import FileBasedExampleGen

from tfx.components import ImporterNode
from tfx.types.standard_artifacts import Schema

from tfx.proto import pusher_pb2
from tfx.proto import trainer_pb2
from tfx.proto import example_gen_pb2

from tensorflow_metadata.proto.v0 import schema_pb2 
from tensorflow_metadata.proto.v0 import statistics_pb2
from tensorflow_metadata.proto.v0 import anomalies_pb2

from ml_metadata import metadata_store
from ml_metadata.proto import metadata_store_pb2

import tensorflow_data_validation as tfdv 
import tensorflow_transform as tft
import tensorflow_model_analysis as tfma

from tfx.types import Channel
from tfx.types.standard_artifacts import Model
from tfx.types.standard_artifacts import ModelBlessing
from tfx.utils.dsl_utils import external_input

/home/jupyter/venv/lib/python3.7/site-packages/tfx/orchestration/data_types.py:191: UserWarning: RuntimeParameter is only supported on KubeflowDagRunner currently.
  warnings.warn('RuntimeParameter is only supported on KubeflowDagRunner '


In [2]:
_data_root_split = "gs://ml-sandbox-tagging-tfx-experiments/data/split_w_genre/"

In [3]:
_pipeline_root = tempfile.mkdtemp(prefix='pipeline')
_pipeline_name = 'interactive_pipeline'

context = InteractiveContext(pipeline_name=_pipeline_name, pipeline_root=_pipeline_root)

In [4]:
input_config = example_gen_pb2.Input(splits=[
                    example_gen_pb2.Input.Split(name='train', pattern='train*'),
                    example_gen_pb2.Input.Split(name='eval', pattern='eval*'),
                    example_gen_pb2.Input.Split(name='new_data', pattern='new*')
])

example_gen = FileBasedExampleGen(input_base=_data_root_split, 
                                  custom_executor_spec=executor_spec.ExecutorClassSpec(parquet_executor.Executor),
                                  input_config=input_config)

context.run(example_gen)

ExecutionResult(
    component_id: FileBasedExampleGen
    execution_id: 1
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 1
        type_id: 5
        uri: "/tmp/pipeline0s7uv1yk/FileBasedExampleGen/examples/1"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:train,num_files:1,total_bytes:31678236,xor_checksum:1609838068,sum_checksum:1609838068\nsplit:eval,num_files:1,total_bytes:2423248,xor_checksum:1609838068,sum_checksum:1609838068\nsplit:new_data,num_files:1,total_bytes:35360785,xor_checksum:1609838070,sum_checksum:1609838070"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

In [5]:
stats_options = tfdv.StatsOptions(num_rank_histogram_buckets=3000)

statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples'],
    stats_options=stats_options)
context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 2
        type_id: 7
        uri: "/tmp/pipeline0s7uv1yk/StatisticsGen/statistics/2"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 7
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [6]:
stats_path = statistics_gen.outputs['statistics'].get()[0].uri
train_statistics_path = os.path.join(stats_path, 'train/stats_tfrecord')
eval_statistics_path = os.path.join(stats_path, 'eval/stats_tfrecord')

train_statistics = tfdv.load_statistics(train_statistics_path)
eval_statistics = tfdv.load_statistics(eval_statistics_path)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


In [7]:
tfdv.visualize_statistics(lhs_statistics=train_statistics,
                          rhs_statistics=eval_statistics)

In [8]:
schema = tfdv.infer_schema(train_statistics, infer_feature_shape=True, max_string_domain_size=3000)

In [9]:
schema.default_environment.append('TRAINING')
schema.default_environment.append('SERVING')

# Genre 
genre = tfdv.get_feature(schema, 'genre')
genre.presence.min_fraction = 0.98 
genre.distribution_constraints.min_domain_mass = 1.0 

genre.skew_comparator.infinity_norm.threshold = 0.05
genre.drift_comparator.infinity_norm.threshold = 0.05

# Tags
tags = tfdv.get_feature(schema, 'series_ep_tags')
tags.presence.min_fraction = 0.98
tags.distribution_constraints.min_domain_mass = 0.99

tags.drift_comparator.infinity_norm.threshold = 0.01
tags.not_in_environment.append('SERVING')

# Features
#tfdv.set_domain(schema, 'features', schema_pb2.StringDomain(name='features', value=[]))

features = tfdv.get_feature(schema, 'features')
features.presence.min_fraction = 1.0
features.distribution_constraints.min_domain_mass = 0.0

In [10]:
eval_anomalies = tfdv.validate_statistics(eval_statistics, schema)

In [11]:
tfdv.display_anomalies(eval_anomalies)

In [12]:
!mkdir ../src/schema

mkdir: cannot create directory ‘../src/schema’: File exists


In [13]:
tfdv.write_schema_text(schema, '../src/schema/schema.pbtxt')

In [14]:
# Import user-provided schema.
schema_importer = ImporterNode(
  instance_name='import_user_schema',
  source_uri='../src/schema/',
  artifact_type=Schema)

context.run(schema_importer)

ExecutionResult(
    component_id: ImporterNode.import_user_schema
    execution_id: 3
    outputs:
        result: Channel(
            type_name: Schema
            artifacts: [Artifact(artifact: id: 3
        type_id: 9
        uri: "../src/schema/"
        , artifact_type: id: 9
        name: "Schema"
        )]
        ))

In [15]:
stats_options = tfdv.StatsOptions(num_rank_histogram_buckets=3000)

statistics_gen_new = StatisticsGen(
    examples=example_gen.outputs['examples'],
    schema=schema_importer.outputs['result'],
    stats_options=stats_options
)
context.run(statistics_gen_new)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 4
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 4
        type_id: 7
        uri: "/tmp/pipeline0s7uv1yk/StatisticsGen/statistics/4"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 7
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [16]:
example_validator_new = ExampleValidator(
      statistics=statistics_gen_new.outputs['statistics'],
      schema=schema_importer.outputs['result'])

context.run(example_validator_new)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 5
    outputs:
        anomalies: Channel(
            type_name: ExampleAnomalies
            artifacts: [Artifact(artifact: id: 5
        type_id: 11
        uri: "/tmp/pipeline0s7uv1yk/ExampleValidator/anomalies/5"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "anomalies"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ExampleValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 11
        name: "ExampleAnomalies"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [17]:
train_anomalies_path = os.path.join(example_validator_new.outputs['anomalies'].get()[-1].uri, 'train/anomalies.pbtxt')
eval_anomalies_path = os.path.join(example_validator_new.outputs['anomalies'].get()[-1].uri, 'eval/anomalies.pbtxt')
new_anomalies_path = os.path.join(example_validator_new.outputs['anomalies'].get()[-1].uri, 'new_data/anomalies.pbtxt')

train_anomalies = tfdv.load_anomalies_text(train_anomalies_path)
eval_anomalies = tfdv.load_anomalies_text(eval_anomalies_path)
new_anomalies = tfdv.load_anomalies_text(new_anomalies_path)

In [18]:
tfdv.display_anomalies(train_anomalies)

In [19]:
tfdv.display_anomalies(eval_anomalies)

In [20]:
tfdv.display_anomalies(new_anomalies)

In [21]:
stats_path = statistics_gen_new.outputs['statistics'].get()[0].uri
train_statistics_path = os.path.join(stats_path, 'train/stats_tfrecord')
eval_statistics_path = os.path.join(stats_path, 'eval/stats_tfrecord')
new_statistics_path = os.path.join(stats_path, 'new_data/stats_tfrecord')

train_statistics_new = tfdv.load_statistics(train_statistics_path)
eval_statistics_new = tfdv.load_statistics(eval_statistics_path)
new_statistics_new = tfdv.load_statistics(new_statistics_path)

In [22]:
eval_drift_anomalies = tfdv.validate_statistics(train_statistics_new, 
                                                previous_statistics=eval_statistics_new, 
                                                schema=schema)

new_data_drift_anomalies = tfdv.validate_statistics(train_statistics_new, 
                                                previous_statistics=new_statistics_new, 
                                                schema=schema)

In [23]:
tfdv.display_anomalies(eval_drift_anomalies)

In [24]:
tfdv.display_anomalies(new_data_drift_anomalies)

/home/jupyter/venv/lib/python3.7/site-packages/tensorflow_data_validation/utils/display_util.py:173: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Anomaly short description  \
Feature name                                                      
'genre'       High Linfty distance between current and previous   

                                                                                                                                                                Anomaly long description  
Feature name                                                                                                                                                                              
'genre'       The Linfty distance between current and previous is 0.0707163 (up to six significant digits), above the threshold 0.05. The feature value with maximum difference is: kids

# **After Transform**

In [27]:
!cp -r ../src/main/ main/

In [28]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=schema_importer.outputs['result'],
    module_file='main/components/transform.py'
)
context.run(transform)

Instructions for updating:
Schema is a deprecated, use schema_utils.schema_from_feature_spec to create a `Schema`
Instructions for updating:
Use ref() instead.


Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
INFO:tensorflow:SavedModel written to: /tmp/pipeline0s7uv1yk/Transform/transform_graph/6/.temp_path/tftransform_tmp/66c6500298d4420597568c51f8f16af8/saved_model.pb
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably 

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:Assets written to: /tmp/pipeline0s7uv1yk/Transform/transform_graph/6/.temp_path/tftransform_tmp/1f99511d370a412e8a7974b420d227f6/assets
INFO:tensorflow:SavedModel written to: /tmp/pipeline0s7uv1yk/Transform/transform_graph/6/.temp_path/tftransform_tmp/1f99511d370a412e8a7974b420d227f6/saved_model.pb
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created 

ExecutionResult(
    component_id: Transform
    execution_id: 6
    outputs:
        transform_graph: Channel(
            type_name: TransformGraph
            artifacts: [Artifact(artifact: id: 6
        type_id: 13
        uri: "/tmp/pipeline0s7uv1yk/Transform/transform_graph/6"
        custom_properties {
          key: "name"
          value {
            string_value: "transform_graph"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 13
        name: "TransformGraph"
        )]
        )
        transformed_examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 7
        type_id: 5
        uri: "/tmp/pipeline0s7uv1yk/Transform/transformed_examples/6"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "transformed_examples"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        )
        updated_analyzer_cache: Channel(
            type_name: TransformCache
            artifacts: [Artifact(artifact: id: 8
        type_id: 14
        uri: "/tmp/pipeline0s7uv1yk/Transform/updated_analyzer_cache/6"
        custom_properties {
          key: "name"
          value {
            string_value: "updated_analyzer_cache"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 14
        name: "TransformCache"
        )]
        ))

In [71]:
transform_dir = transform.outputs['transform_graph'].get()[0].uri
transformed_schema = tfdv.load_schema_text(os.path.join(transform_dir, 'transformed_metadata', 'schema.pbtxt'))

tfdv.display_schema(transformed_schema)

Type  Presence Valency      Domain
Feature name                                         
'features_xf'     INT    required          [0,128948]
'series_ep_tags'  BYTES                    -

In [37]:
stats_options = tfdv.StatsOptions(num_histogram_buckets=100)

transform_statistics_gen = StatisticsGen(
    examples=transform.outputs['transformed_examples'],
    stats_options=stats_options)
context.run(transform_statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 8
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 10
        type_id: 7
        uri: "/tmp/pipeline0s7uv1yk/StatisticsGen/statistics/8"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"new_data\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 7
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [67]:
stats_path = transform_statistics_gen.outputs['statistics'].get()[0].uri
transformed_train_statistics_path = os.path.join(stats_path, 'train/stats_tfrecord')
transformed_eval_statistics_path = os.path.join(stats_path, 'eval/stats_tfrecord')
transformed_new_statistics_path = os.path.join(stats_path, 'new_data/stats_tfrecord')

transformed_train_statistics = tfdv.load_statistics(transformed_train_statistics_path)
transformed_eval_statistics = tfdv.load_statistics(transformed_eval_statistics_path)
transformed_new_statistics = tfdv.load_statistics(transformed_new_statistics_path)

In [68]:
tfdv.visualize_statistics(transformed_train_statistics, transformed_new_statistics)

In [72]:
tfdv.get_feature(transformed_schema, 'features_xf').drift_comparator.jensen_shannon_divergence.threshold = 0.05

In [76]:
anomalies = tfdv.validate_statistics(transformed_train_statistics, 
                        schema=transformed_schema,
                        previous_statistics=transformed_eval_statistics)

In [77]:
tfdv.display_anomalies(anomalies)

In [78]:
anomalies = tfdv.validate_statistics(transformed_train_statistics, 
                        schema=transformed_schema,
                        previous_statistics=transformed_new_statistics)

In [79]:
tfdv.display_anomalies(anomalies)

/home/jupyter/venv/lib/python3.7/site-packages/tensorflow_data_validation/utils/display_util.py:173: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Anomaly short description  \
Feature name                                                                             
'features_xf'  High approximate Jensen-Shannon divergence between current and previous   

                                                                                                                                   Anomaly long description  
Feature name                                                                                                                                                 
'features_xf'  The approximate Jensen-Shannon divergence between current and previous is 0.184569 (up to six significant digits), above the threshold 0.05.

In [80]:
tfdv.write_schema_text(transformed_schema, '../src/schema/transformed_schema.pbtxt')